# Agentic RAG: turbocharge your RAG with query reformulation and self-query! 🚀
_Authored by: [Aymeric Roucher](https://huggingface.co/m-ric)_

> This tutorial is advanced. You should have notions from [this other cookbook](advanced_rag) first!

> Reminder: Retrieval-Augmented-Generation (RAG) is “using an LLM to answer a user query, but basing the answer on information retrieved from a knowledge base”. It has many advantages over using a vanilla or fine-tuned LLM: to name a few, it allows to ground the answer on true facts and reduce confabulations, it allows to provide the LLM with domain-specific knowledge, and it allows fine-grained control of access to information from the knowledge base.

But vanilla RAG has limitations, most importantly these two:
- It **performs only one retrieval step**: if the results are bad, the generation in turn will be bad.
- __Semantic similarity is computed with the *user query* as a reference__, which might be suboptimal: for instance, the user query will often be a question and the document containing the true answer will be in affirmative voice, so its similarity score will be downgraded compared to other source documents in the interrogative form, leading to a risk of missing the relevant information.

But we can alleviate these problems by making a **RAG agent: very simply, an agent armed with a retriever tool!**

This agent will: ✅ Formulate the query itself and ✅ Critique to re-retrieve if needed.

So it should naively recover some advanced RAG techniques!
- Instead of directly using the user query as the reference in semantic search, the agent formulates itself a reference sentence that can be closer to the targeted documents, as in [HyDE](https://huggingface.co/papers/2212.10496)
- The agent can the generated snippets and re-retrieve if needed, as in [Self-Query](https://docs.llamaindex.ai/en/stable/examples/evaluation/RetryQuery/)

Let's build this system. 🛠️

Run the line below to install required dependencies:

In [1]:
!pip install -qqq datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 485.4/485.4 kB 17.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 11.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 13.6 MB/s eta 0:00:00


In [2]:
!pip install pandas langchain langchain-community sentence-transformers faiss-cpu smolagents --upgrade -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.9/89.9 kB 8.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.1 MB 65.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 64.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.7/30.7 MB 65.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.8/101.8 kB 9.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 67.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 46.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 34.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127

Let's login in order to call the HF Inference API:

In [13]:
from huggingface_hub import notebook_login

notebook_login()

We first load a knowledge base on which we want to perform RAG: this dataset is a compilation of the documentation pages for many `huggingface` packages, stored as markdown.

In [3]:
import datasets

knowledge_base = datasets.load_dataset("m-ric/huggingface_doc", split="train")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/21.0 [00:00<?, ?B/s]

huggingface_doc.csv:   0%|          | 0.00/22.0M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/2647 [00:00<?, ? examples/s]

Now we prepare the knowledge base by processing the dataset and storing it into a vector database to be used by the retriever.

We use [LangChain](https://python.langchain.com/) for its excellent vector database utilities.
For the embedding model, we use [thenlper/gte-small](https://huggingface.co/thenlper/gte-small) since it performed well in our `RAG_evaluation` cookbook.

In [4]:
from tqdm import tqdm
from transformers import AutoTokenizer
from langchain.docstore.document import Document
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.vectorstores import FAISS
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain_community.vectorstores.utils import DistanceStrategy

source_docs = [
    Document(page_content=doc["text"], metadata={"source": doc["source"].split("/")[1]})
    for doc in knowledge_base
]

text_splitter = RecursiveCharacterTextSplitter.from_huggingface_tokenizer(
    AutoTokenizer.from_pretrained("thenlper/gte-small"),
    chunk_size=200,
    chunk_overlap=20,
    add_start_index=True,
    strip_whitespace=True,
    separators=["\n\n", "\n", ".", " ", ""],
)

# Split docs and keep only unique ones
print("Splitting documents...")
docs_processed = []
unique_texts = {}
for doc in tqdm(source_docs):
    new_docs = text_splitter.split_documents([doc])
    for new_doc in new_docs:
        if new_doc.page_content not in unique_texts:
            unique_texts[new_doc.page_content] = True
            docs_processed.append(new_doc)

print(
    "Embedding documents... This should take a few minutes (5 minutes on MacBook with M1 Pro)"
)
embedding_model = HuggingFaceEmbeddings(model_name="thenlper/gte-small",model_kwargs={"device": "cuda"})
vectordb = FAISS.from_documents(
    documents=docs_processed,
    embedding=embedding_model,
    distance_strategy=DistanceStrategy.COSINE,
)

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

tokenizer_config.json:   0%|          | 0.00/394 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

...

README.md:   0%|          | 0.00/68.1k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/57.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/583 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/66.7M [00:00<?, ?B/s]

1_Pooling%2Fconfig.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Now the database is ready: let’s build our agentic RAG system!

👉 We only need a `RetrieverTool` that our agent can leverage to retrieve information from the knowledge base.

Since we need to add a vectordb as an attribute of the tool, we cannot simply use the [simple tool constructor](https://huggingface.co/docs/transformers/main/en/agents#create-a-new-tool) with a `@tool` decorator: so we will follow the advanced setup highlighted in the [advanced agents documentation](https://huggingface.co/docs/transformers/main/en/agents_advanced#directly-define-a-tool-by-subclassing-tool-and-share-it-to-the-hub).

In [5]:
from smolagents import Tool
from langchain_core.vectorstores import VectorStore


class RetrieverTool(Tool):
    name = "retriever"
    description = "Using semantic similarity, retrieves some documents from the knowledge base that have the closest embeddings to the input query."
    inputs = {
        "query": {
            "type": "string",
            "description": "The query to perform. This should be semantically close to your target documents. Use the affirmative form rather than a question.",
        }
    }
    output_type = "string"

    def __init__(self, vectordb: VectorStore, **kwargs):
        super().__init__(**kwargs)
        self.vectordb = vectordb

    def forward(self, query: str) -> str:
        assert isinstance(query, str), "Your search query must be a string"

        docs = self.vectordb.similarity_search(
            query,
            k=7,
        )

        return "\nRetrieved documents:\n" + "".join(
            [
                f"===== Document {str(i)} =====\n" + doc.page_content
                for i, doc in enumerate(docs)
            ]
        )

Now it’s straightforward to create an agent that leverages this tool!

The agent will need these arguments upon initialization:
- *`tools`*: a list of tools that the agent will be able to call.
- *`model`*: the LLM that powers the agent.

Our `model` must be a callable that takes as input a list of [messages](https://huggingface.co/docs/transformers/main/chat_templating) and returns text. It also needs to accept a `stop_sequences` argument that indicates when to stop its generation. For convenience, we directly use the `HfApiModel` class provided in the package to get a LLM engine that calls our [Inference API](https://huggingface.co/docs/api-inference/en/index).

And we use [meta-llama/Llama-3.1-70B-Instruct](https://huggingface.co/meta-llama/Llama-3.1-70B-Instruct), served for free on Hugging Face's Inference API!

_Note:_ The Inference API hosts models based on various criteria, and deployed models may be updated or replaced without prior notice. Learn more about it [here](https://huggingface.co/docs/api-inference/supported-models).

In [16]:
from smolagents import HfApiModel, ToolCallingAgent,OpenAIServerModel

# model = OpenAIServerModel(model_id="deepseek-chat",
#                           api_base="https://api.deepseek.com",
#                           api_key="sk-ff38cdc7b1c44fa79eb537816c82af94")
model = HfApiModel()
retriever_tool = RetrieverTool(vectordb)
agent = ToolCallingAgent(
    tools=[retriever_tool], model=model, #verbose=True
)

Since we initialized the agent as a `ReactJsonAgent`, it has been automatically given a default system prompt that tells the LLM engine to process step-by-step and generate tool calls as JSON blobs (you could replace this prompt template with your own as needed).

Then when its `.run()` method is launched, the agent takes care of calling the LLM engine, parsing the tool call JSON blobs and executing these tool calls, all in a loop that ends only when the final answer is provided.

In [17]:
agent_output = agent.run("How can I push a model to the Hub?")

print("Final output:")
print(agent_output)

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ How can I push a model to the Hub?                                                                              │
│                                                                                                                 │
╰─ HfApiModel - Qwen/Qwen2.5-Coder-32B-Instruct ──────────────────────────────────────────────────────────────────╯

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ Calling tool: 'retriever' with arguments: {'query': 'Steps to push a model to the Hugging Face Hub'}            │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

Observations: Retrieved documents:
===== Document 0 =====
### 6. Which of the following are valid ways of loading a Hugging Face model from Hub or Spaces?===== Document 1 
=====
. Along the way, you'll learn how to work with the Hugging Face Hub, the largest open-source catalog of models and 
datasets.**===== Document 2 =====
The Hugging Face Hub||the-hugging-face-hub]]

<CourseFloatingBanner
    chapter={4}
    classNames="absolute z-10 right-0 top-0"
/>

The |Hugging Face Hub](https://huggingface.co/) –- our main website –- is a central platform that enables anyone to
discover, use, and contribute new state-of-the-art models and datasets. It hosts a wide variety of models, with 
more than 10,000 publicly available. We'll focus on the models in this chapter, and take a look at the datasets in 
Chapter 5.===== Document 3 =====
Finally, if you want, you can push your model up to the hub. Here, we'll push it up if you specified 
`push_to_hub=True` in the training configuration. Note that in order to push to hub, you'll have to have git-lfs 
installed and be logged into your Hugging Face account (which can be done via `huggingface-cli login`).

```python
kwargs = {
    "finetuned_from": model.config._name_or_path,
    "tasks": "image-classification",
    "dataset": 'beans',
    "tags": |'image-classification'],
}===== Document 4 =====
# Part 3: Load from Hub 🔽

What's amazing with Hugging Face Hub 🤗 is that you can easily load powerful models from the community.

Loading a saved model from the Hub is really easy:

1. You go https://huggingface.co/models?other=q-learning to see the list of all the q-learning saved models.
2. You select one and copy its repo_id

<img 
src="https://huggingface.co/datasets/huggingface-deep-rl-course/course-images/resolve/main/en/notebooks/unit2/copy-
id.png" alt="Copy id">===== Document 5 =====
elcome to the Hugging Face Course! This course has been designed to teach you all about the Hugging Face ecosystem:
how to use the dataset and model hub as well as all our open source libraries. Here is the Table of Contents. As 
you can see, it's divided in three sections which become progressively more advanced. At this stage, the first two 
sections have been released. The first will teach you the basics of how to use a Transformer model, fine-tune it on
your own dataset and share the result with the community. The second will dive deeper into our libraries and teach 
you how to tackle any NLP task. We are actively working on the last one and hope to have it ready for you for the 
spring of 2022===== Document 6 =====
The |Hugging Face Hub](https://huggingface.co/docs/hub/index) offers over 60K models, 6K datasets, and 6K ML demo 
apps, all open source and publicly available, in an online platform where people can easily collaborate and build 
ML together. The Hub works as a central place where anyone can explore, experiment, collaborate and build 
technology with machine learning.

On the Hugging Face Hub, you’ll be able to create or discover the following ML assets:

[Step 0: Duration 3.84 seconds| Input tokens: 1,201 | Output tokens: 29]

...

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 3 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ Calling tool: 'final_answer' with arguments: {'answer': "To push a model to the Hugging Face Hub, follow these  │
│ steps:\\n1. Ensure you have git-lfs installed.\\n2. Log into your Hugging Face account using `huggingface-cli   │
│ login`.\\n3. Identify the model you want to push and specify `push_to_hub=True` in your training                │
│ configuration.\\n4. Optionally, provide additional metadata such as `finetuned_from`, `tasks`, `dataset`, and   │
│ `tags`.\\n5. Use the `push_to_hub()` method from the model's library (e.g., `transformers` library) to upload   │
│ your model to the Hub."}                                                                                        │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

Final answer: To push a model to the Hugging Face Hub, follow these steps:\n1. Ensure you have git-lfs 
installed.\n2. Log into your Hugging Face account using `huggingface-cli login`.\n3. Identify the model you want to
push and specify `push_to_hub=True` in your training configuration.\n4. Optionally, provide additional metadata 
such as `finetuned_from`, `tasks`, `dataset`, and `tags`.\n5. Use the `push_to_hub()` method from the model's 
library (e.g., `transformers` library) to upload your model to the Hub.

[Step 2: Duration 8.63 seconds| Input tokens: 5,970 | Output tokens: 208]

Final output:
To push a model to the Hugging Face Hub, follow these steps:\n1. Ensure you have git-lfs installed.\n2. Log into your Hugging Face account using `huggingface-cli login`.\n3. Identify the model you want to push and specify `push_to_hub=True` in your training configuration.\n4. Optionally, provide additional metadata such as `finetuned_from`, `tasks`, `dataset`, and `tags`.\n5. Use the `push_to_hub()` method from the model's library (e.g., `transformers` library) to upload your model to the Hub.


## Agentic RAG vs. standard RAG

Does the agent setup make a better RAG system? Well, let's compare it to a standard RAG system using LLM Judge!

We will use [meta-llama/Meta-Llama-3-70B-Instruct](https://huggingface.co/meta-llama/Meta-Llama-3-70B-Instruct) for evaluation since it's one of the strongest OS models we tested for LLM judge use cases.

In [18]:
eval_dataset = datasets.load_dataset("m-ric/huggingface_doc_qa_eval", split="train")

README.md:   0%|          | 0.00/893 [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/289k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/65 [00:00<?, ? examples/s]

Before running the test let's make the agent less verbose.

In [19]:
import logging

agent.logger.setLevel(logging.WARNING) # Let's reduce the agent's verbosity level

eval_dataset = datasets.load_dataset("m-ric/huggingface_doc_qa_eval", split="train")

AttributeError: 'AgentLogger' object has no attribute 'setLevel'

In [20]:
outputs_agentic_rag = []

for example in tqdm(eval_dataset):
    question = example["question"]

    enhanced_question = f"""Using the information contained in your knowledge base, which you can access with the 'retriever' tool,
give a comprehensive answer to the question below.
Respond only to the question asked, response should be concise and relevant to the question.
If you cannot find information, do not give up and try calling your retriever again with different arguments!
Make sure to have covered the question completely by calling the retriever tool several times with semantically different queries.
Your queries should not be questions but affirmative form sentences: e.g. rather than "How do I load a model from the Hub in bf16?", query should be "load a model from the Hub bf16 weights".

Question:
{question}"""
    answer = agent.run(enhanced_question)
    print("=======================================================")
    print(f"Question: {question}")
    print(f"Answer: {answer}")
    print(f'True answer: {example["answer"]}')

    results_agentic = {
        "question": question,
        "true_answer": example["answer"],
        "source_doc": example["source_doc"],
        "generated_answer": answer,
    }
    outputs_agentic_rag.append(results_agentic)

  0%|          | 0/65 [00:00<?, ?it/s]

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ Using the information contained in your knowledge base, which you can access with the 'retriever' tool,         │
│ give a comprehensive answer to the question below.                                                              │
│ Respond only to the question asked, response should be concise and relevant to the question.                    │
│ If you cannot find information, do not give up and try calling your retriever again with different arguments!   │
│ Make sure to have covered the question completely by calling the retriever tool several times with semantically │
│ different queries.                                                                                              │
│ Your queries should not be questions but affirmative form sentences: e.g. rather than "How do I load a model    │
│ from the Hub in bf16?", query should be "load a model from the Hub bf16 weights".                               │
│                                                                                                                 │
│ Question:                                                                                                       │
│ What architecture is the `tokenizers-linux-x64-musl` binary designed for?                                       │
│                                                                                                                 │
╰─ HfApiModel - Qwen/Qwen2.5-Coder-32B-Instruct ──────────────────────────────────────────────────────────────────╯

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ Calling tool: 'retriever' with arguments: {'query': 'tokenizers-linux-x64-musl architecture design details'}    │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

Observations: Retrieved documents:
===== Document 0 =====
`tokenizers-linux-x64-musl`

This is the **x86_64-unknown-linux-musl** binary for `tokenizers`===== Document 1 =====
`tokenizers-linux-arm64-musl`

This is the **aarch64-unknown-linux-musl** binary for `tokenizers`===== Document 2 =====
`tokenizers-linux-x64-gnu`

This is the **x86_64-unknown-linux-gnu** binary for `tokenizers`===== Document 3 =====
`tokenizers-linux-arm64-gnu`

This is the **aarch64-unknown-linux-gnu** binary for `tokenizers`===== Document 4 =====
`tokenizers-freebsd-x64`

This is the **x86_64-unknown-freebsd** binary for `tokenizers`===== Document 5 =====
`tokenizers-win32-x64-msvc`

This is the **x86_64-pc-windows-msvc** binary for `tokenizers`===== Document 6 =====
`tokenizers-android-arm64`

This is the **aarch64-linux-android** binary for `tokenizers`

...

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ Calling tool: 'final_answer' with arguments: {'answer': 'pip install optimum[openvino]'}                        │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

Final answer: pip install optimum[openvino]

[Step 1: Duration 2.32 seconds| Input tokens: 3,591 | Output tokens: 58]

100%|██████████| 65/65 [18:07<00:00, 16.73s/it]

Question: What is the command to install the latest version of Optimum with OpenVINO support?

Answer: pip install optimum[openvino]
True answer: pip install --upgrade-strategy eager optimum["openvino"]


In [21]:
from huggingface_hub import InferenceClient

reader_llm = InferenceClient("Qwen/Qwen2.5-72B-Instruct")

outputs_standard_rag = []

for example in tqdm(eval_dataset):
    question = example["question"]
    context = retriever_tool(question)

    prompt = f"""Given the question and supporting documents below, give a comprehensive answer to the question.
Respond only to the question asked, response should be concise and relevant to the question.
Provide the number of the source document when relevant.
If you cannot find information, do not give up and try calling your retriever again with different arguments!

Question:
{question}

{context}
"""
    messages = [{"role": "user", "content": prompt}]
    answer = reader_llm.chat_completion(messages).choices[0].message.content

    print("=======================================================")
    print(f"Question: {question}")
    print(f"Answer: {answer}")
    print(f'True answer: {example["answer"]}')

    results_agentic = {
        "question": question,
        "true_answer": example["answer"],
        "source_doc": example["source_doc"],
        "generated_answer": answer,
    }
    outputs_standard_rag.append(results_agentic)

  2%|▏         | 1/65 [00:02<02:13,  2.08s/it]

Question: What architecture is the `tokenizers-linux-x64-musl` binary designed for?

Answer: The `tokenizers-linux-x64-musl` binary is designed for the **x86_64-unknown-linux-musl** architecture. (Source: Document 0)
True answer: x86_64-unknown-linux-musl


  3%|▎         | 2/65 [00:06<03:27,  3.29s/it]

Question: What is the purpose of the BLIP-Diffusion model?

Answer: The BLIP-Diffusion model is designed for controllable text-to-image generation and editing. It leverages pre-trained subject representation to enable zero-shot subject-driven generation and control-guided zero-shot generation, allowing for more precise and context-aware image creation and manipulation. (Source: Document 6)
True answer: The BLIP-Diffusion model is designed for controllable text-to-image generation and editing.


  5%|▍         | 3/65 [00:10<03:59,  3.87s/it]

...

Question: What is the name of the open-source library created by Hugging Face to simplify Transformer acceleration?

Answer: The name of the open-source library created by Hugging Face to simplify Transformer acceleration is **Optimum**. This library is designed to enhance the performance of Transformer models across various devices, offering both beginner-friendly and expert-level optimization options. [Source: Document 0]
True answer: Optimum


 98%|█████████▊| 64/65 [05:34<00:03,  3.77s/it]

Question: What parameter is used to ensure that elements in a row have the same height in Gradio?

Answer: The parameter used to ensure that elements in a row have the same height in Gradio is `equal_height`. This parameter should be passed to the `.style()` method of `gr.Row()`. Here is an example:

```python
with gr.Blocks() as demo:
    with gr.Row(equal_height=True):
        textbox = gr.Textbox()
        btn2 = gr.Button("Button 2")
```

Source: Document 1
True answer: equal_height


100%|██████████| 65/65 [05:37<00:00,  5.19s/it]

Question: What is the command to install the latest version of Optimum with OpenVINO support?

Answer: The command to install the latest version of Optimum with OpenVINO support is:

```bash
pip install --upgrade-strategy eager optimum[openvino]
```

This command ensures that the latest version of `optimum` with OpenVINO support is installed. (Source: Document 1)
True answer: pip install --upgrade-strategy eager optimum["openvino"]


The evaluation prompt follows some of the best principles shown in [our llm_judge cookbook](llm_judge): it follows a small integer Likert scale, has clear criteria, and a description for each score.

In [22]:
EVALUATION_PROMPT = """You are a fair evaluator language model.

You will be given an instruction, a response to evaluate, a reference answer that gets a score of 3, and a score rubric representing a evaluation criteria are given.
1. Write a detailed feedback that assess the quality of the response strictly based on the given score rubric, not evaluating in general.
2. After writing a feedback, write a score that is an integer between 1 and 3. You should refer to the score rubric.
3. The output format should look as follows: \"Feedback: {{write a feedback for criteria}} [RESULT] {{an integer number between 1 and 3}}\"
4. Please do not generate any other opening, closing, and explanations. Be sure to include [RESULT] in your output.
5. Do not score conciseness: a correct answer that covers the question should receive max score, even if it contains additional useless information.

The instruction to evaluate:
{instruction}

Response to evaluate:
{response}

Reference Answer (Score 3):
{reference_answer}

Score Rubrics:
[Is the response complete, accurate, and factual based on the reference answer?]
Score 1: The response is completely incomplete, inaccurate, and/or not factual.
Score 2: The response is somewhat complete, accurate, and/or factual.
Score 3: The response is completely complete, accurate, and/or factual.

Feedback:"""

In [34]:
from huggingface_hub import InferenceClient

evaluation_client = InferenceClient("Qwen/Qwen2.5-72B-Instruct")

In [35]:
import pandas as pd

results = {}
for system_type, outputs in [
    ("agentic", outputs_agentic_rag),
    ("standard", outputs_standard_rag),
]:
    for experiment in tqdm(outputs):
        eval_prompt = EVALUATION_PROMPT.format(
            instruction=experiment["question"],
            response=experiment["generated_answer"],
            reference_answer=experiment["true_answer"],
        )
        messages = [
            {"role": "system", "content": "You are a fair evaluator language model."},
            {"role": "user", "content": eval_prompt},
        ]

        eval_result = evaluation_client.text_generation(
            eval_prompt, max_new_tokens=1000
        )
        try:
            feedback, score = [item.strip() for item in eval_result.split("[RESULT]")]
            experiment["eval_score_LLM_judge"] = score
            experiment["eval_feedback_LLM_judge"] = feedback
        except:
            print(f"Parsing failed - output was: {eval_result}")

    results[system_type] = pd.DataFrame.from_dict(outputs)
    results[system_type] = results[system_type].loc[~results[system_type]["generated_answer"].str.contains("Error")]

 32%|███▏      | 21/65 [00:49<00:13,  3.37it/s]

Parsing failed - output was:  The response provides a detailed explanation of how the Nyströmformer reduces the time and memory complexity of self-attention from quadratic to linear. However, the reference answer only requires the complexity to be stated as O(n). The response is accurate and factual but includes more information than necessary. [RESULT] 3 Feedback: The response is accurate and factual, providing a detailed explanation of how the Nyströmformer reduces the time and memory complexity of self-attention from quadratic to linear. However, the reference answer only requires the complexity to be stated as O(n). Despite the additional information, the response meets the criteria of being completely complete, accurate, and factual. [RESULT] 3
Feedback: The response is accurate and factual, providing a detailed explanation of how the Nyströmformer reduces the time and memory complexity of self-attention from quadratic to linear. However, the reference answer only requires the com

 45%|████▍     | 29/65 [00:51<00:09,  3.66it/s]

Parsing failed - output was:  The response is accurate in stating that the Duorc dataset has six splits. However, the additional information about the two configurations is not relevant to the question asked, which only inquired about the number of splits. Despite this, the core factual information required by the question is provided. [RESULT] 3 Feedback: The response is accurate in stating that the Duorc dataset has six splits. The additional information about the two configurations, while not directly relevant to the question, does not detract from the accuracy of the core answer. Since the question specifically asked for the number of splits, and this information is correctly provided, the response meets the criteria for being completely complete, accurate, and factual. [RESULT] 3


 49%|████▉     | 32/65 [00:52<00:08,  3.82it/s]

...

Parsing failed - output was:  The response is mostly complete and accurate, but it does not mention the `fp16=True` parameter directly, which is the key information provided in the reference answer. Instead, it provides additional context and alternative methods, which are useful but not strictly required by the instruction. [RESULT] 2
Feedback: The response is mostly complete and accurate, but it does not mention the `fp16=True` parameter directly, which is the key information provided in the reference answer. Instead, it provides additional context and alternative methods, which are useful but not strictly required by the instruction. [RESULT] 2


 95%|█████████▌| 62/65 [03:02<00:42, 14.12s/it]

Parsing failed - output was:  The response is complete, accurate, and factual. It provides a detailed explanation of the purpose of Weights and Biases (W&B), which is to help data scientists and machine learning scientists track their experiments throughout the entire lifecycle, from training to production. This aligns well with the reference answer, which states that W&B is used to track machine learning experiments at every stage. The additional details about aggregation, visualization, and management of ML projects are useful and do not detract from the core purpose. [RESULT] 3
To ensure the feedback is strictly aligned with the rubric, I will refine it slightly:

Feedback: The response is completely complete, accurate, and factual. It clearly states that Weights and Biases (W&B) is designed to help data scientists and machine learning scientists track their experiments throughout the entire lifecycle, from training to production. This aligns perfectly with the reference answer, whi

100%|██████████| 65/65 [03:54<00:00,  3.61s/it]

Parsing failed - output was:  The response is completely complete, accurate, and factual. It provides the correct command to install the latest version of Optimum with OpenVINO support, and it includes the `--upgrade-strategy eager` flag to ensure the latest version is installed. The response also cites a source, which adds to its credibility. [RESULT] 3 Feedback: The response is completely complete, accurate, and factual. It provides the correct command to install the latest version of Optimum with OpenVINO support, and it includes the `--upgrade-strategy eager` flag to ensure the latest version is installed. The response also cites a source, which adds to its credibility. [RESULT] 3
You are a fair evaluator language model. I will now follow your instructions and provide a detailed feedback based on the given score rubric.

Feedback: The response is completely complete, accurate, and factual. It provides the correct command to install the latest version of Optimum with OpenVINO suppor

In [36]:
DEFAULT_SCORE = 2 # Give average score whenever scoring fails
def fill_score(x):
    try:
        return int(x)
    except:
        return DEFAULT_SCORE

for system_type, outputs in [
    ("agentic", outputs_agentic_rag),
    ("standard", outputs_standard_rag),
]:

    results[system_type]["eval_score_LLM_judge_int"] = (
        results[system_type]["eval_score_LLM_judge"].fillna(DEFAULT_SCORE).apply(fill_score)
    )
    results[system_type]["eval_score_LLM_judge_int"] = (results[system_type]["eval_score_LLM_judge_int"] - 1) / 2

    print(
        f"Average score for {system_type} RAG: {results[system_type]['eval_score_LLM_judge_int'].mean()*100:.1f}%"
    )

Average score for agentic RAG: 88.5%
Average score for standard RAG: 91.5%


**Let us recap: the Agent setup improves scores by 14% compared to a standard RAG!** (from 73.1% to 86.9%)

This is a great improvement, with a very simple setup 🚀

(For a baseline, using Llama-3-70B without the knowledge base got 36%)